![header](../figures/logos_partenaires._cmems_se.jpg)

# North Atlantic: Benchmark NIO-WOC plot maps
 

***
**Authors:**  CLS & Datlas <br>
**Copyright:** 2023 CLS & Datlas <br>
**License:** MIT

<div class="alert alert-block alert-success">
<h1><center>North Atlantic: Benchmark of NIO-WOC plot maps</center></h1>
<h5> The notebook aims to plot maps produced by the DUACS system. </h5>
    <h5> These maps are equivalent to the SEALEVEL_GLO_PHY_L4_MY_008_047 product distributed by the Copernicus Marine Service, except that a nadir altimeter (SARAL/Altika, SEALEVEL_GLO_PHY_L3_MY_008_062 product) has been excluded from the mapping. </h5>
        <h5> We provide below a demonstration of the validation of these maps against the independent SSH data from the Saral/AltiKa altimeter distributed by CMEMS </h5>
</div>

***
**General Note 1**: Execute each cell through the <button class="btn btn-default btn-xs"><i class="icon-play fa fa-play"></i></button> button from the top MENU (or keyboard shortcut `Shift` + `Enter`).<br>
<br>
**General Note 2**: If, for any reason, the kernel is not working anymore, in the top MENU, click on the <button class="btn btn-default btn-xs"><i class="fa fa-repeat icon-repeat"></i></button> button. Then, in the top MENU, click on "Cell" and select "Run All Above Selected Cell".<br>
***


<div class="alert alert-danger" role="alert">

<h3>Learning outcomes</h3>

At the end of this notebook you will know:
<ul>
  <li>How you can evaluated sea surface height maps with independent alongtrack data: statistical and spectral analysis</li>
</ul>
    
</div>

In [1]:
from glob import glob
import numpy as np
import os

In [2]:
import sys
sys.path.append('..')
from src.mod_plot import *
from src.mod_stat import *
from src.mod_spectral import *
from src.mod_interp import *
from src.mod_switchvar import *

In [3]:
import logging
logger = logging.getLogger()
logger.setLevel(logging.INFO)

<div class="alert alert-info" role="alert">

<h2>0. Parameters</h2>

</div>

In [4]:
time_min = '2019-01-01'                                        # time min for analysis
time_max = '2019-12-31'                                        # time max for analysis
output_dir = '../results'                                      # output directory path
os.system(f'mkdir -p {output_dir}')

# Gulf Stream region
region = 'NA'
lon_min = -100                                          # domain min longitude
lon_max = 20                                          # domain max longitude
lat_min = 0.                                          # domain min latitude
lat_max = 70.                                          # domain max latitude
box_lonlat = {'lon_min':lon_min,'lon_max':lon_max,'lat_min':lat_min,'lat_max':lat_max}

method_name = 'NIO-WOC'


<div class="alert alert-info" role="alert">

<h2>1. Input files</h2>

</div>

## Sea Surface Height maps to evaluate

In [5]:
%%time
list_of_maps = sorted(glob('../data/maps/WOC_products/*.nc'))
ds_maps = xr.open_mfdataset(list_of_maps, combine='nested', concat_dim='time')
ds_maps = ds_maps.sel(time=slice(time_min, time_max))
ds_maps

CPU times: user 6.21 s, sys: 800 ms, total: 7.01 s
Wall time: 8.56 s


<xarray.Dataset>
Dimensions:                     (lon: 481, lat: 281, time: 8760, depth: 1)
Coordinates:
  * lon                         (lon) float32 -100.0 -99.75 -99.5 ... 19.75 20.0
  * lat                         (lat) float32 0.0 0.25 0.5 ... 69.5 69.75 70.0
  * time                        (time) datetime64[ns] 2019-01-01 ... 2019-12-...
  * depth                       (depth) float64 15.0
Data variables:
    eastward_eulerian_current   (time, depth, lat, lon) float32 dask.array<chunksize=(24, 1, 281, 481), meta=np.ndarray>
    northward_eulerian_current  (time, depth, lat, lon) float32 dask.array<chunksize=(24, 1, 281, 481), meta=np.ndarray>
Attributes: (12/50)
    Conventions:                   CF-1.7, ACDD-1.3, ISO 8601
    Metadata_Conventions:          Climate and Forecast (CF) 1.7, Attribute C...
    standard_name_vocabulary:      NetCDF Climate and Forecast (CF) Metadata ...
    title:                         North Altantic Total Surface Current for E...
    summary:                       This dataset contains the total surface cu...
    id:                            WOC-L4-CUReul-ENATL-1H
    ...                            ...
    date_modified:                 11/05/2022
    source:                        
    source_version:                
    history:                       
    input:                         ERA5 (neutral surface winds) and  CMEMS MU...
    processing_software:

In [6]:
# Rename u and v
ds_maps = ds_maps.rename_vars({'eastward_eulerian_current':'ugos','northward_eulerian_current':'vgos'})

# Remove unnecessary depth dimension
ds_maps = ds_maps.isel({'depth':0})

# Rename lon and lat
ds_maps = ds_maps.rename({'lon':'longitude','lat':'latitude'})

# Averaging to have daily currents
ds_maps = ds_maps.resample(time='1D').mean(dim='time')

## Selecting only North Atlantic

In [7]:

from src.mod_compare import regional_zoom

ds_maps = regional_zoom(ds_maps, [box_lonlat['lon_min'],box_lonlat['lon_max']], [box_lonlat['lat_min'],box_lonlat['lat_max']], namelon='longitude', namelat='latitude', change_lon=True)
ds_maps

<xarray.Dataset>
Dimensions:    (time: 365, latitude: 279, longitude: 479)
Coordinates:
  * longitude  (longitude) float32 -99.75 -99.5 -99.25 ... 19.25 19.5 19.75
  * latitude   (latitude) float32 0.25 0.5 0.75 1.0 ... 69.0 69.25 69.5 69.75
    depth      float64 15.0
  * time       (time) datetime64[ns] 2019-01-01 2019-01-02 ... 2019-12-31
Data variables:
    ugos       (time, latitude, longitude) float32 dask.array<chunksize=(1, 279, 479), meta=np.ndarray>
    vgos       (time, latitude, longitude) float32 dask.array<chunksize=(1, 279, 479), meta=np.ndarray>
Attributes: (12/50)
    Conventions:                   CF-1.7, ACDD-1.3, ISO 8601
    Metadata_Conventions:          Climate and Forecast (CF) 1.7, Attribute C...
    standard_name_vocabulary:      NetCDF Climate and Forecast (CF) Metadata ...
    title:                         North Altantic Total Surface Current for E...
    summary:                       This dataset contains the total surface cu...
    id:                            WOC-L4-CUReul-ENATL-1H
    ...                            ...
    date_modified:                 11/05/2022
    source:                        
    source_version:                
    history:                       
    input:                         ERA5 (neutral surface winds) and  CMEMS MU...
    processing_software:

## Plot NIO-WOC geostrophic currents movie

In [8]:
movie(ds_maps,name_var='uv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[0,1.2],cmap='viridis', newmovie=True)


## Compute and plot NIO-WOC relative vorticity movie

In [10]:
rv = currents_to_relative_vorticity(np.array(ds_maps.ugos),np.array(ds_maps.vgos), ds_maps.longitude,ds_maps.latitude)

ds_maps = ds_maps.assign(rv=lambda ds_maps: ds_maps.ugos * 0 + rv)

ds_maps.rv.attrs = {'grid_mapping': 'crs',
                    'long_name': 'Geostrophic relative vorticity',
                    'standard_name': 'surface_geostrophic_relative_vorticity',
                    'units': 'adim'}

In [11]:
movie(ds_maps,name_var='rv', method=method_name, region=region, dir_output='../results/',dim_name=['time','latitude','longitude'],
          framerate=24,Display=True,clim=[-0.5,0.5],cmap='coolwarm', newmovie=True)
